In [1]:
import numpy as np
import pandas as pd
import xgboost as xgb

from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import log_loss

import optuna
from optuna import Trial, visualization

import warnings
warnings.filterwarnings("ignore")

In [2]:
train = pd.read_csv('/kaggle/input/primal2-0/final_train.csv')
test = pd.read_csv('/kaggle/input/primal2-0/final_test.csv')
CandidateID = test['CandidateID']

In [3]:


import pandas as pd
from sklearn.preprocessing import OneHotEncoder
import re

# Load train and test data
train_data = pd.read_csv('/kaggle/input/primal2-0/final_train.csv')
test_data = pd.read_csv('/kaggle/input/primal2-0/final_test.csv')

# Concatenate train and test data for preprocessing
combined_data = pd.concat([train_data, test_data], ignore_index=True)

value_mapping = {
    'a': 6,  # Example: 10 lakhs
}
# Replace values in the 'ticket size' column using the mapping
combined_data['Previous_Organizations'] = test_data['Previous_Organizations'].replace(value_mapping)

# Drop specified columns
combined_data.drop(columns=['Designation', 'DOJ', 'R_District', 'B_District', 'Company_1', 'Company_2', 'Skill'], inplace=True)

# Replace Graduation and Qualification values
combined_data['Graduation'] = combined_data['Graduation'].fillna(0).map({'full time': 1, 'part time': 0, 0: 0})
combined_data['Qualification'] = combined_data['Qualification'].map({'graduate': 2, 'under graduate': 1, 'post graduate': 3, 'others': 0, 'diploma holders': 4}).fillna(-1)

# Set 'Previous_Organizations' as type int, treating NaN as 0
combined_data['Previous_Organizations'] = combined_data['Previous_Organizations'].fillna(0).astype(int)

# One-hot encoding for categorical variables
columns_to_encode = ['Industry', 'Source', 'Department', 'R_Region', 'B_Region']
combined_data_encoded = pd.get_dummies(combined_data, columns=columns_to_encode)

# Create indicator variables for states
states = list(combined_data['R_State']) + list(combined_data['B_State'])
for state in states:
    combined_data_encoded[state] = ((combined_data['R_State'] == state) | (combined_data['B_State'] == state)).astype(int)

# Drop 'R_State' and 'B_State'
combined_data_encoded.drop(columns=['R_State', 'B_State', 'Unnamed: 0'], inplace=True)
combined_data_encoded.columns = [re.sub(r'\W+', '_', col) for col in combined_data_encoded.columns]

# Separate back into train and test data
train_data_processed = combined_data_encoded.iloc[:len(train_data)]
test_data_processed = combined_data_encoded.iloc[len(train_data):].drop(columns='Performance')  # Assuming 'Target' is the target column



In [4]:
train = train_data_processed
test = test_data_processed

In [5]:
train.head()

CandidateID  Graduation  Qualification  Experience  Previous_Organizations  \
0     emp0669           1            2.0         5.0                       6   
1     emp0273           1            2.0         1.5                       4   
2     emp0300           1            1.0         4.5                       2   
3     emp0100           1            3.0         4.5                       4   
4     emp0319           1            3.0         1.0                       2   

   Incentive  Ticket_Size  Family_Members  Earning_Members  Dependent_Members  \
0      12000      1000000               2              1.0                  1   
1       8000       150000               4              2.0                  4   
2      20000      2000000               4              1.0                  2   
3      12000      2000000               4              2.0                  3   
4          0            0               4              1.0                  3   

   ...  rajasthan  himachal_pradesh  punjab  assam  haryana  chandigarh  \
0  ...          0                 0       0      0        0           0   
1  ...          0                 0       0      0        0           0   
2  ...          0                 0       0      0        0           0   
3  ...          0                 0       0      0        0           0   
4  ...          0                 0       0      0        0           0   

   west_bengal  jharkhand  jammu_and_kashmir  bihar  
0            0          0                  0      0  
1            0          0                  0      0  
2            0          0                  0      0  
3            0          0                  0      0  
4            0          0                  0      0  

[5 rows x 188 columns]

In [6]:
feature_cols = [col for col in train.columns.tolist() if col not in ['CandidateID', 'Performance']]
target_col = ['Performance']

In [7]:


class_dict = {
    0: 0,
    1: 1,
}



In [8]:
train['Performance'] = train['Performance'].map(class_dict)

In [9]:


skf = StratifiedKFold(n_splits=5, random_state=42, shuffle=True)

for i, (trn, val) in enumerate(skf.split(train, train[target_col])):
    train.loc[val, 'kfold'] = i
train['kfold'] = train['kfold'].astype(int)



In [10]:
from catboost import CatBoostClassifier, Pool

def fit_catboost(trial, xtr, ytr, xval, yval, categorical_features=None):
  """
  Fits a CatBoost model with hyperparameter tuning using Optuna trial.

  Args:
      trial: Optuna trial object for hyperparameter suggestions.
      xtr: Training data (features).
      ytr: Training target labels.
      xval: Validation data (features).
      yval: Validation target labels.
      categorical_features: List of indices for categorical features (optional).

  Returns:
      A tuple containing the fitted CatBoost model and a dictionary with training and validation metrics.
  """

  params = {
      "iterations": trial.suggest_int("iterations", 100, 500),  # Number of trees
      "learning_rate": trial.suggest_loguniform("learning_rate", 1e-3, 0.1),  # Learning rate
      "depth": trial.suggest_int("depth", 4, 10),  # Tree depth
      "l2_leaf_reg": trial.suggest_loguniform("l2_leaf_reg", 1e-3, 10),  # L2 regularization
      "subsample": trial.suggest_discrete_uniform("subsample", 0.5, 1, 0.1),  # Subsample ratio
      "colsample_bylevel": trial.suggest_discrete_uniform("colsample_bylevel", 0.5, 1, 0.1),  # Feature subsample by level
      "random_strength": trial.suggest_int("random_strength", 1, 6),  # Randomization strength
  }

  if categorical_features is not None:
      train_pool = Pool(xtr, ytr, cat_features=categorical_features)
      val_pool = Pool(xval, yval, cat_features=categorical_features)
  else:
      train_pool = Pool(xtr, ytr)
      val_pool = Pool(xval, yval)

  model = CatBoostClassifier(**params, random_state=42)
  model.fit(train_pool)

  y_val_pred = model.predict_proba(xval)

  y_val_pred = model.predict_proba(xval)
    
  log = {
        "train logloss": log_loss(ytr, model.predict_proba(xtr)),
        "valid logloss": log_loss(yval, y_val_pred)
    }
    
  return model, log

In [11]:
def objective(trial):
    loss = 0
    for fold in range(5):
        trn_idx = train['kfold'] != fold
        val_idx = train['kfold'] == fold
        trn = train.loc[trn_idx, :]
        val = train.loc[val_idx, :]

        xtr, ytr = trn[feature_cols].values, trn[target_col].values
        xval, yval = val[feature_cols].values, val[target_col].values
        
        model, log = fit_catboost(trial, xtr, ytr, xval, yval)
        loss += log['valid logloss']/5
        
    return loss

In [12]:
study = optuna.create_study(direction="minimize", study_name='Catboost optimization')
study.optimize(objective, n_trials=100)

[I 2024-04-11 07:38:06,379] A new study created in memory with name: Catboost optimization


0:	learn: 0.6923259	total: 69.4ms	remaining: 12.4s
1:	learn: 0.6916454	total: 88.3ms	remaining: 7.81s
2:	learn: 0.6894625	total: 102ms	remaining: 5.99s
3:	learn: 0.6883932	total: 118ms	remaining: 5.16s
4:	learn: 0.6877791	total: 130ms	remaining: 4.52s
5:	learn: 0.6870839	total: 140ms	remaining: 4.05s
6:	learn: 0.6854356	total: 152ms	remaining: 3.73s
7:	learn: 0.6838172	total: 164ms	remaining: 3.51s
8:	learn: 0.6826968	total: 176ms	remaining: 3.33s
9:	learn: 0.6818257	total: 187ms	remaining: 3.16s
10:	learn: 0.6806476	total: 198ms	remaining: 3.02s
11:	learn: 0.6799217	total: 209ms	remaining: 2.91s
12:	learn: 0.6793506	total: 221ms	remaining: 2.83s
13:	learn: 0.6787103	total: 233ms	remaining: 2.75s
14:	learn: 0.6779441	total: 246ms	remaining: 2.69s
15:	learn: 0.6763577	total: 260ms	remaining: 2.65s
16:	learn: 0.6754135	total: 271ms	remaining: 2.58s
17:	learn: 0.6740782	total: 282ms	remaining: 2.52s
18:	learn: 0.6735198	total: 292ms	remaining: 2.46s
19:	learn: 0.6725206	total: 302ms	remai

[I 2024-04-11 07:38:17,326] Trial 0 finished with value: 0.6633883073672726 and parameters: {'iterations': 179, 'learning_rate': 0.0018077047601994982, 'depth': 9, 'l2_leaf_reg': 0.011319997981762432, 'subsample': 0.7, 'colsample_bylevel': 0.6, 'random_strength': 1}. Best is trial 0 with value: 0.6633883073672726.


0:	learn: 0.6929867	total: 1.66ms	remaining: 354ms
1:	learn: 0.6928947	total: 2.57ms	remaining: 272ms
2:	learn: 0.6925235	total: 3.83ms	remaining: 269ms
3:	learn: 0.6923446	total: 5.05ms	remaining: 265ms
4:	learn: 0.6921737	total: 6.13ms	remaining: 256ms
5:	learn: 0.6918800	total: 7.26ms	remaining: 252ms
6:	learn: 0.6917644	total: 8.13ms	remaining: 241ms
7:	learn: 0.6915930	total: 9.29ms	remaining: 239ms
8:	learn: 0.6913418	total: 10.4ms	remaining: 237ms
9:	learn: 0.6912132	total: 11.5ms	remaining: 235ms
10:	learn: 0.6910693	total: 12.5ms	remaining: 231ms
11:	learn: 0.6909238	total: 13.6ms	remaining: 229ms
12:	learn: 0.6908307	total: 14.2ms	remaining: 220ms
13:	learn: 0.6906159	total: 15.2ms	remaining: 217ms
14:	learn: 0.6904547	total: 16.2ms	remaining: 215ms
15:	learn: 0.6902420	total: 17.3ms	remaining: 214ms
16:	learn: 0.6900909	total: 18.4ms	remaining: 213ms
17:	learn: 0.6898774	total: 19.4ms	remaining: 212ms
18:	learn: 0.6897248	total: 20.5ms	remaining: 211ms
19:	learn: 0.6896189	t

[I 2024-04-11 07:38:19,415] Trial 1 finished with value: 0.6729109529830578 and parameters: {'iterations': 214, 'learning_rate': 0.002076206430581389, 'depth': 5, 'l2_leaf_reg': 1.825055852067149, 'subsample': 1.0, 'colsample_bylevel': 0.5, 'random_strength': 2}. Best is trial 0 with value: 0.6633883073672726.


...

158:	learn: 0.4133483	total: 223ms	remaining: 19.6ms
159:	learn: 0.4113537	total: 225ms	remaining: 18.3ms
160:	learn: 0.4093352	total: 227ms	remaining: 16.9ms
161:	learn: 0.4078732	total: 229ms	remaining: 15.5ms
162:	learn: 0.4069733	total: 230ms	remaining: 14.1ms
163:	learn: 0.4031584	total: 231ms	remaining: 12.7ms
164:	learn: 0.4007922	total: 233ms	remaining: 11.3ms
165:	learn: 0.3986443	total: 234ms	remaining: 9.88ms
166:	learn: 0.3964408	total: 236ms	remaining: 8.46ms
167:	learn: 0.3945448	total: 237ms	remaining: 7.05ms
168:	learn: 0.3923395	total: 239ms	remaining: 5.64ms
169:	learn: 0.3900664	total: 240ms	remaining: 4.24ms
170:	learn: 0.3879093	total: 242ms	remaining: 2.83ms
171:	learn: 0.3859934	total: 243ms	remaining: 1.41ms
172:	learn: 0.3846905	total: 245ms	remaining: 0us
0:	learn: 0.6893039	total: 1.66ms	remaining: 196ms
1:	learn: 0.6861193	total: 3.28ms	remaining: 192ms
2:	learn: 0.6790956	total: 4.69ms	remaining: 181ms
3:	learn: 0.6742742	total: 6.12ms	remaining: 176ms
4:	l

[I 2024-04-11 07:44:39,760] Trial 98 finished with value: 0.6423935110744214 and parameters: {'iterations': 119, 'learning_rate': 0.06438603842259566, 'depth': 5, 'l2_leaf_reg': 1.5554032521756225, 'subsample': 0.9, 'colsample_bylevel': 0.9, 'random_strength': 5}. Best is trial 92 with value: 0.6356738439435765.


0:	learn: 0.6885226	total: 1.31ms	remaining: 194ms
1:	learn: 0.6834753	total: 2.77ms	remaining: 204ms
2:	learn: 0.6801805	total: 3.77ms	remaining: 183ms
3:	learn: 0.6756323	total: 4.82ms	remaining: 175ms
4:	learn: 0.6703006	total: 5.85ms	remaining: 169ms
5:	learn: 0.6658860	total: 6.92ms	remaining: 165ms
6:	learn: 0.6631590	total: 7.94ms	remaining: 161ms
7:	learn: 0.6610417	total: 8.98ms	remaining: 158ms
8:	learn: 0.6586026	total: 10ms	remaining: 156ms
9:	learn: 0.6549412	total: 11ms	remaining: 153ms
10:	learn: 0.6530937	total: 12.1ms	remaining: 151ms
11:	learn: 0.6492907	total: 13.1ms	remaining: 149ms
12:	learn: 0.6476730	total: 14.1ms	remaining: 147ms
13:	learn: 0.6462661	total: 15.1ms	remaining: 145ms
14:	learn: 0.6433925	total: 16.1ms	remaining: 144ms
15:	learn: 0.6407646	total: 17.1ms	remaining: 142ms
16:	learn: 0.6394653	total: 18.2ms	remaining: 141ms
17:	learn: 0.6374600	total: 19.3ms	remaining: 140ms
18:	learn: 0.6369266	total: 20.2ms	remaining: 138ms
19:	learn: 0.6356423	total

[I 2024-04-11 07:44:41,288] Trial 99 finished with value: 0.6481868545485371 and parameters: {'iterations': 149, 'learning_rate': 0.08379061372077265, 'depth': 4, 'l2_leaf_reg': 3.271700953322302, 'subsample': 0.8, 'colsample_bylevel': 0.8, 'random_strength': 5}. Best is trial 92 with value: 0.6356738439435765.


0:	learn: 0.6839035	total: 1.19ms	remaining: 177ms
1:	learn: 0.6798268	total: 2.5ms	remaining: 184ms
2:	learn: 0.6762297	total: 3.42ms	remaining: 167ms
3:	learn: 0.6726094	total: 4.28ms	remaining: 155ms
4:	learn: 0.6706223	total: 5.15ms	remaining: 148ms
5:	learn: 0.6676461	total: 6.04ms	remaining: 144ms
6:	learn: 0.6652164	total: 6.9ms	remaining: 140ms
7:	learn: 0.6611066	total: 7.83ms	remaining: 138ms
8:	learn: 0.6597986	total: 8.72ms	remaining: 136ms
9:	learn: 0.6566813	total: 9.64ms	remaining: 134ms
10:	learn: 0.6547020	total: 10.5ms	remaining: 132ms
11:	learn: 0.6522172	total: 11.5ms	remaining: 131ms
12:	learn: 0.6489066	total: 12.3ms	remaining: 129ms
13:	learn: 0.6480730	total: 13.2ms	remaining: 128ms
14:	learn: 0.6464224	total: 14.1ms	remaining: 126ms
15:	learn: 0.6447473	total: 15ms	remaining: 124ms
16:	learn: 0.6431454	total: 15.9ms	remaining: 123ms
17:	learn: 0.6416289	total: 16.7ms	remaining: 122ms
18:	learn: 0.6382513	total: 17.6ms	remaining: 120ms
19:	learn: 0.6344204	total

In [13]:
params = study.best_params

In [14]:
train_pool = Pool(train[feature_cols], train[target_col])
model = CatBoostClassifier(**params, random_state=42)
model.fit(train_pool)

0:	learn: 0.6879964	total: 1.82ms	remaining: 243ms
1:	learn: 0.6846051	total: 3.63ms	remaining: 239ms
2:	learn: 0.6803595	total: 5.01ms	remaining: 219ms
3:	learn: 0.6763518	total: 6.56ms	remaining: 213ms
4:	learn: 0.6725316	total: 7.91ms	remaining: 204ms
5:	learn: 0.6698721	total: 9.43ms	remaining: 201ms
6:	learn: 0.6669597	total: 10.9ms	remaining: 198ms
7:	learn: 0.6642815	total: 12.3ms	remaining: 193ms
8:	learn: 0.6627653	total: 13.2ms	remaining: 184ms
9:	learn: 0.6593501	total: 14.6ms	remaining: 182ms
10:	learn: 0.6576975	total: 16ms	remaining: 179ms
11:	learn: 0.6565787	total: 17.4ms	remaining: 177ms
12:	learn: 0.6537105	total: 18.7ms	remaining: 174ms
13:	learn: 0.6520971	total: 20.1ms	remaining: 172ms
14:	learn: 0.6513788	total: 21.4ms	remaining: 170ms
15:	learn: 0.6503536	total: 22.8ms	remaining: 168ms
16:	learn: 0.6486694	total: 24.3ms	remaining: 167ms
17:	learn: 0.6468915	total: 25.8ms	remaining: 166ms
18:	learn: 0.6454945	total: 27.2ms	remaining: 164ms
19:	learn: 0.6435610	tot

In [15]:
test_predictions = model.predict_proba(test[feature_cols])

In [16]:
predictions_df = pd.DataFrame(test_predictions, columns = ["Class_1", "Class_2"])
predictions_df['CandidateID'] = CandidateID

In [17]:
predictions_df['CandidateID'] = list(CandidateID)
predictions_df

Class_1   Class_2 CandidateID
0    0.499127  0.500873     emp0521
1    0.506849  0.493151     emp0613
2    0.500227  0.499773     emp0136
3    0.672314  0.327686     emp0351
4    0.700939  0.299061     emp0049
..        ...       ...         ...
182  0.481385  0.518615     emp0401
183  0.853676  0.146324     emp0408
184  0.541968  0.458032     emp0248
185  0.532569  0.467431     emp0148
186  0.439187  0.560813     emp0422

[187 rows x 3 columns]

In [18]:
predictions_df.to_csv('Catboost_D.csv')